In [1]:
import pandas as pd
import requests
from bs4 import BeautifulSoup
import re
from tqdm import tqdm
import time

In [2]:
MAIN_URL = "https://pl.wikisource.org/"
URL_YELLOW = "https://pl.wikisource.org/wiki/Kategoria:Skorygowana"
URL_GREEN = "https://pl.wikisource.org/wiki/Kategoria:Uwierzytelniona"

In [3]:
def get_page_data(page_element):
    doc = requests.get(MAIN_URL + page_element['href'])
    doc_soup = BeautifulSoup(doc.text, 'lxml', from_encoding="utf-8")
    text_elem = doc_soup.find("div", {"class": "pagetext"}).next_element
    text = text_elem.text 
    image_url = doc_soup.find("div", {"class": "prp-page-image"}).next_element['src']
    return {"title": page_element['title'], "href": MAIN_URL + page_element['href'], "image_url": image_url, "text": text,}


In [4]:
r  = requests.get(URL_YELLOW)
soup = BeautifulSoup(r.text, 'lxml')

In [5]:
"".join(re.findall("\d", re.sub("\xa0",'', soup.find("div", {"id": "mw-pages"}).find("p").text))[3:])

'107478'

In [6]:
links = soup.find_all("a", {"href": re.compile(r"\/wiki\/Strona:.*")})

In [15]:
next_page = soup.find("a", {"href": re.compile(r"\/w\/index.php.*")}, string="następna strona")

In [7]:
get_page_data(links[0])

c:\Users\PC\anaconda3\envs\um\lib\site-packages\bs4\__init__.py:226: UserWarning: You provided Unicode markup but also provided a value for from_encoding. Your from_encoding will be ignored.
  warnings.warn("You provided Unicode markup but also provided a value for from_encoding. Your from_encoding will be ignored.")


{'title': 'Strona:A. Baranowski - O wzorach.pdf/7',
 'href': 'https://pl.wikisource.org//wiki/Strona:A._Baranowski_-_O_wzorach.pdf/7',
 'image_url': '//upload.wikimedia.org/wikipedia/commons/thumb/7/7e/A._Baranowski_-_O_wzorach.pdf/page7-1024px-A._Baranowski_-_O_wzorach.pdf.jpg',
 'text': '\u2009Potem napisałem teoryę luk, których Dr. Hossfeld nie podjął się sprawdzić.\n\u2009Nareszcie usunąwszy wszystkie liczby podzielne przez \n\n\n\n2\n,\n\n\n{\\displaystyle 2,}\n\n \n\n\n\n3\n\n\n{\\displaystyle 3}\n\n i \n\n\n\n5\n\n\n{\\displaystyle 5}\n\n, jako łatwe do poznania, zanalizowałem zakres numeracyi \n\n\n\n0\n,\n\n\n{\\displaystyle 0,}\n\n \n\n\n\n1\n,\n\n\n{\\displaystyle 1,}\n\n \n\n\n\n2\n,\n\n\n{\\displaystyle 2,}\n\n \n\n\n\n3\n,\n…\n\n\n{\\displaystyle 3,\\ldots }\n\n \n\n\n\n150\n\n060\n\n\n{\\displaystyle 150\\,060}\n\n, czyli liczby wszystkie pierwsze w tym zakresie, oraz podzielne przez \n\n\n\n7\n,\n\n\n{\\displaystyle 7,}\n\n \n\n\n\n11\n,\n\n\n{\\displaystyle 11,}\n\n \n

In [5]:

page_number = 1
result_list = []
max_len = "".join(re.findall("\d", re.sub("\xa0",'', soup.find("div", {"id": "mw-pages"}).find("p").text))[3:])
try:
    while True:
        next_page = soup.find("a", {"href": re.compile(r"\/w\/index.php.*")}, string="następna strona").get('href', None)
        if next_page and page_number != 1:
            r = requests.get(MAIN_URL + next_page)
        else:
            break

        if r.status_code != 200:
            print(r.__dict__)
            break
        soup = BeautifulSoup(r.text, 'lxml')
        page_number += 1
        links = soup.find_all("a", {"href": re.compile(r"\/wiki\/Strona:.*")})
        for link in tqdm(links):
            result_list.append(get_page_data(link))
        print("Page number:", page_number)
        print("Number of elements:", 200 * page_number, "/", max_len)
except Exception as e:
    print(e)
    df = pd.DataFrame(result_list)
    df.to_csv("./yellow.tsv", sep="\t")

df = pd.DataFrame(result_list)
df.to_csv("./yellow.tsv", sep="\t")

  0%|          | 0/200 [00:00<?, ?it/s]c:\Users\PC\anaconda3\envs\um\lib\site-packages\bs4\__init__.py:226: UserWarning: You provided Unicode markup but also provided a value for from_encoding. Your from_encoding will be ignored.
  warnings.warn("You provided Unicode markup but also provided a value for from_encoding. Your from_encoding will be ignored.")
100%|██████████| 200/200 [02:15<00:00,  1.47it/s]


Page number: 2
Number of elements: 200 / 107477


100%|██████████| 200/200 [02:05<00:00,  1.60it/s]


Page number: 3
Number of elements: 400 / 107477


In [18]:
MAIN_URL + next_page['href']

'https://pl.wikisource.org//w/index.php?title=Kategoria:Skorygowana&pagefrom=Aleksander+B%C5%82a%C5%BCejowski+-+S%C4%85d+nad+Antychrystem.pdf%2F22%0AAleksander+B%C5%82a%C5%BCejowski+-+S%C4%85d+nad+Antychrystem.pdf%2F22#mw-pages'

In [5]:
get_page_data(soup.find_all("a", {"href": re.compile(r"\/wiki\/Strona:.*")})[25])

c:\Users\PC\anaconda3\envs\um\lib\site-packages\bs4\__init__.py:226: UserWarning: You provided Unicode markup but also provided a value for from_encoding. Your from_encoding will be ignored.
  warnings.warn("You provided Unicode markup but also provided a value for from_encoding. Your from_encoding will be ignored.")


{'title': 'Strona:Adam Mickiewicz - Dziady część III.djvu/199',
 'href': 'https://pl.wikisource.org//wiki/Strona:Adam_Mickiewicz_-_Dziady_cz%C4%99%C5%9B%C4%87_III.djvu/199',
 'image_url': '//upload.wikimedia.org/wikipedia/commons/thumb/8/8f/Adam_Mickiewicz_-_Dziady_cz%C4%99%C5%9B%C4%87_III.djvu/page199-1024px-Adam_Mickiewicz_-_Dziady_cz%C4%99%C5%9B%C4%87_III.djvu.jpg',
 'text': '\nTy najwięcéj zgrzeszyłeś: kary nie wyminiesz;\nLecz ostatni, najgłośniéj, najhaniebniéj zginiesz.[1]\n\nA druga powieść taka. Za czasu dawnego,\n\xa0\xa0\xa0\xa0\xa0\xa0\xa0585\nPewny wódz rzymski pobił króla potężnego;\nI kazał na śmierć zabić wszystkie niewolniki,[2]\nWszystkie rotmistrze półków i wszystkie setniki:\nAle króla samego przy życiu zostawił,\nTudzież starosty, tudzież półkowniki zbawił. —[3]\n\xa0\xa0\xa0\xa0\xa0\xa0\xa0590\nI mówili do siebie głupi więźnie owi:\nBędziem żyć, podziękujmy za życie wodzowi.\nAż jeden żołnierz rzymski, co im posługował,\nRzekł im: zaprawdę, wódz was przy życiu zac

In [79]:
all_docs_on_page = soup.find_all("a", {"href": re.compile(r"\/wiki\/Strona:.*")})
result = []
for doc in tqdm(all_docs_on_page[:10]):
    result.append(get_page_data(doc))

100%|██████████| 10/10 [00:06<00:00,  1.61it/s]


In [80]:
result

[{'title': 'Strona:A. Baranowski - O wzorach.pdf/7',
  'href': 'https://pl.wikisource.org//wiki/Strona:A._Baranowski_-_O_wzorach.pdf/7',
  'image_url': '//upload.wikimedia.org/wikipedia/commons/thumb/7/7e/A._Baranowski_-_O_wzorach.pdf/page7-1024px-A._Baranowski_-_O_wzorach.pdf.jpg',
  'text': '\u2009Potem napisałem teoryę luk, których Dr. Hossfeld nie podjął się sprawdzić.\n\u2009Nareszcie usunąwszy wszystkie liczby podzielne przez \n\n\n\n2\n,\n\n\n{\\displaystyle 2,}\n\n \n\n\n\n3\n\n\n{\\displaystyle 3}\n\n i \n\n\n\n5\n\n\n{\\displaystyle 5}\n\n, jako łatwe do poznania, zanalizowałem zakres numeracyi \n\n\n\n0\n,\n\n\n{\\displaystyle 0,}\n\n \n\n\n\n1\n,\n\n\n{\\displaystyle 1,}\n\n \n\n\n\n2\n,\n\n\n{\\displaystyle 2,}\n\n \n\n\n\n3\n,\n…\n\n\n{\\displaystyle 3,\\ldots }\n\n \n\n\n\n150\n\n060\n\n\n{\\displaystyle 150\\,060}\n\n, czyli liczby wszystkie pierwsze w tym zakresie, oraz podzielne przez \n\n\n\n7\n,\n\n\n{\\displaystyle 7,}\n\n \n\n\n\n11\n,\n\n\n{\\displaystyle 11,}\n\